# Trips - preparing
Broad to-do:
- few quick fixes for stop and route names
- consolidate csv to one trip per row (takes a long time)
- ~~generate gtfs trips.txt and stop_times.txt~~ > doing in tsrtc10
- save the per-trip grouping to a csv so it can be loaded up by other programs.

In [1]:
import pandas as pd
from collections import OrderedDict
import numpy as np
import openpyxl
import os.path
from ast import literal_eval # for parsing list stored as string back into list


/mnt/7ACA0CC0CA0C7B21/temp/py36/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


In [2]:
# loading the file
df = pd.read_csv('TSRTC-alldepots-ORIG.csv', dtype=str).fillna('')
# typecasting all columns as text, so that concat etc operations are simpler to do further along.
print(df.shape)
df.columns

(437060, 28)


Index(['DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER', 'TRIP_ID',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME', 'STAGE_TYPE',
       'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'TO_TIME', 'BREAK_TIME',
       'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE', 'OD_WED', 'OD_THU', 'OD_FRI',
       'OD_SAT', 'OD_SUN', 'DATA_ORDR'],
      dtype='object')

## some quick fixes from routes experience

In [3]:
df.ROUTE_NUMBER.replace('','BLANK',inplace=True)

In [4]:
# data cleaning
# first, find them
df[ df.ROUTE_NUMBER != df.ROUTE_NUMBER.str.strip() ].ROUTE_NUMBER.unique()

array([' 212/568'], dtype=object)

In [5]:
df[ df.CURRENT_STAGE_NAME != df.CURRENT_STAGE_NAME.str.strip() ].CURRENT_STAGE_NAME.unique()
# bloody hell there's tabs n shit in the stops! will have to fix this in the stops tables too.

array(['S.R.NAGAR\t', 'EENADU\t', 'MUNICIPAL OFFICE\t', 'ECIL\t',
       'AGRICULTURAL COLLEGE        \t'], dtype=object)

In [6]:
# rest colummns are fine. now, cleaning
df.ROUTE_NUMBER = df.ROUTE_NUMBER.apply(lambda x: x.strip())
df.CURRENT_STAGE_NAME = df.CURRENT_STAGE_NAME.apply(lambda x: x.strip())

In [7]:
# check again..
df[ df.CURRENT_STAGE_NAME != df.CURRENT_STAGE_NAME.str.strip() ].CURRENT_STAGE_NAME.unique()

array([], dtype=object)

In [8]:
# check for commas in name
df[ df.CURRENT_STAGE_NAME.str.contains(',') ].CURRENT_STAGE_NAME.unique()
# holy shit one exists

array(['SRIDEVI- ENGG,COLLEGE'], dtype=object)

In [9]:
'#'*100

'####################################################################################################'

## grouping by trip_id

In [10]:
# using the custom function approach to do all the grouping and processing at a go.
def listORone(ser):
    return list(ser) if len(set(ser))>1 else ser.iloc[0]

def trip_grouping(x):
    names = {
        'DEPOT_CODE': listORone(x['DEPOT_CODE']),
        'SERVICE_ID': listORone(x['SERVICE_ID']),
        'SERVICE_NO': listORone(x['SERVICE_NO']),
        'SERVICE_TYPE': listORone(x['SERVICE_TYPE']),
        'DAY_NIGHT_OUT': listORone(x['DAY_NIGHT_OUT']),
        'SCHEDULE_DAYS': listORone(x['SCHEDULE_DAYS']),
        'ROUTE_ID': listORone(x['ROUTE_ID']),
        'ROUTE_NUMBER': listORone(x['ROUTE_NUMBER']),
        # 'TRIP_ID': listORone(x['TRIP_ID']),
        'TRIP_NUM': listORone(x['TRIP_NUM']),
        'TRIP_TYPE': listORone(x['TRIP_TYPE']),
        'STAGE_ID': listORone(x['STAGE_ID']),
        'CURRENT_STAGE_NAME': listORone(x['CURRENT_STAGE_NAME']),
        'STAGE_TYPE': listORone(x['STAGE_TYPE']),
        'DISTANCE': listORone(x['DISTANCE']),
        'TIME_DISTANCE': listORone(x['TIME_DISTANCE']),
        
        # exception for FROM_TIME : need to keep that in an array.
        'FROM_TIME': list(x['FROM_TIME']),
        
        'TO_TIME': listORone(x['TO_TIME']),
        'BREAK_TIME': listORone(x['BREAK_TIME']),
        'OPERATIONAL_DAYS': listORone(x['OPERATIONAL_DAYS']),
        'OD_MON': listORone(x['OD_MON']),
        'OD_TUE': listORone(x['OD_TUE']),
        'OD_WED': listORone(x['OD_WED']),
        'OD_THU': listORone(x['OD_THU']),
        'OD_FRI': listORone(x['OD_FRI']),
        'OD_SAT': listORone(x['OD_SAT']),
        'OD_SUN': listORone(x['OD_SUN']),
        
        # extra columns:
        'num_stops': len(x),
        'first_time': x['FROM_TIME'].iloc[0]
    }
    return pd.Series(names, index=['DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME','num_stops', 'STAGE_TYPE',
       'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'first_time','TO_TIME', 'BREAK_TIME',
       'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE', 'OD_WED', 'OD_THU', 'OD_FRI',
       'OD_SAT', 'OD_SUN'])        

In [11]:
tripsGroup1 = df.groupby(['TRIP_ID']).apply(trip_grouping).reset_index()
tripsGroup1.head()

TRIP_ID DEPOT_CODE SERVICE_ID SERVICE_NO SERVICE_TYPE DAY_NIGHT_OUT  \
0     100        KCG         60       0292           SN             D   
1  100059        MI2    6707965       2201           CS             D   
2  100060        MI2    6707965       2201           CS             D   
3  100081        MI2    6707965       2201           CS             D   
4  100082        MI2    6707965       2201           CS             D   

  SCHEDULE_DAYS ROUTE_ID ROUTE_NUMBER TRIP_NUM  ...   TO_TIME BREAK_TIME  \
0             1      115           2J        7  ...     21:15      00:00   
1             2    18131         222L        1  ...     07:49      00:00   
2             2    18131         222L        2  ...     09:19      00:00   
3             2    18131         222L        3  ...     11:19      00:30   
4             2    18131         222L        4  ...     13:19      00:30   

  OPERATIONAL_DAYS  OD_MON OD_TUE OD_WED OD_THU OD_FRI OD_SAT OD_SUN  
0                6       Y      Y      Y      Y      Y      Y      Y  
1                7       Y      Y      Y      Y      Y      Y      Y  
2                7       Y      Y      Y      Y      Y      Y      Y  
3                7       Y      Y      Y      Y      Y      Y      Y  
4                7       Y      Y      Y      Y      Y      Y      Y  

[5 rows x 29 columns]

In [12]:
# this one takes a LONG time. So, let's split the notebook here, export output as csv.
tripsGroup1.to_csv('grouped-tripwise-raw.csv', index_label='sr')

In [13]:
'#'*100

'####################################################################################################'